In [9]:
import anndata

example_sce = anndata.read_h5ad("data/million_cells.h5ad", backed=True, chunk_size=int(2e4))

We can set the flag below to True to run on the full, on-disk dataset. Otherwise, this notebook uses a small on-disk dataset, just so that it can run quickly.

In [10]:
run_full = False

This dataset has 1.4 million cells. We'll read 20K cells into memory at a time.

In [11]:
example_sce.obs

celltype majorType     City  sampleID  \
AACAGGGGTCGGATTT-0        Mono_c1-CD14-CCL3      Mono   Zhuhai  S-S070-1   
AACCAACGTCCGAAAG-0         B_c02-MS4A1-CD27         B   Zhuhai  S-S070-1   
AACCTTTGTAGCACGA-0              B_c01-TCL1A         B   Zhuhai  S-S070-1   
AAGCATCTCTATCGCC-0    Mono_c2-CD14-HLA-DPB1      Mono   Zhuhai  S-S070-1   
AATCACGGTCATAAAG-0              B_c01-TCL1A         B   Zhuhai  S-S070-1   
...                                     ...       ...      ...       ...   
TTTGTCATCCACGCAG-283                   Mega      Mega  Beijing    S-S053   
TTTGTCATCCGCTGTT-283            B_c06-MKI67    Plasma  Beijing    S-S053   
TTTGTCATCGTCGTTC-283         T_CD8_c01-LEF1       CD8  Beijing    S-S053   
TTTGTCATCTGTACGA-283          NK_c01-FCGR3A        NK  Beijing    S-S053   
TTTGTCATCTTGCCGT-283       T_CD8_c05-ZNF683       CD8  Beijing    S-S053   

                     donor_id  Sample type CoVID-19 severity  Sample time  \
AACAGGGGTCGGATTT-0     P-S070  frozen PBMC   severe/critical  progression   
AACCAACGTCCGAAAG-0     P-S070  frozen PBMC   severe/critical  progression   
AACCTTTGTAGCACGA-0     P-S070  frozen PBMC   severe/critical  progression   
AAGCATCTCTATCGCC-0     P-S070  frozen PBMC   severe/critical  progression   
AATCACGGTCATAAAG-0     P-S070  frozen PBMC   severe/critical  progression   
...                       ...          ...               ...          ...   
TTTGTCATCCACGCAG-283   P-S053  frozen PBMC   severe/critical  progression   
TTTGTCATCCGCTGTT-283   P-S053  frozen PBMC   severe/critical  progression   
TTTGTCATCGTCGTTC-283   P-S053  frozen PBMC   severe/critical  progression   
TTTGTCATCTGTACGA-283   P-S053  frozen PBMC   severe/critical  progression   
TTTGTCATCTTGCCGT-283   P-S053  frozen PBMC   severe/critical  progression   

                     Sampling day (Days after symptom onset)  \
AACAGGGGTCGGATTT-0                                         7   
AACCAACGTCCGAAAG-0                                         7   
AACCTTTGTAGCACGA-0                                         7   
AAGCATCTCTATCGCC-0                                         7   
AATCACGGTCATAAAG-0                                         7   
...                                                      ...   
TTTGTCATCCACGCAG-283                                       9   
TTTGTCATCCGCTGTT-283                                       9   
TTTGTCATCGTCGTTC-283                                       9   
TTTGTCATCTGTACGA-283                                       9   
TTTGTCATCTTGCCGT-283                                       9   

                     BCR single cell sequencing  ... tissue_type  \
AACAGGGGTCGGATTT-0                           No  ...      tissue   
AACCAACGTCCGAAAG-0                           No  ...      tissue   
AACCTTTGTAGCACGA-0                           No  ...      tissue   
AAGCATCTCTATCGCC-0                           No  ...      tissue   
AATCACGGTCATAAAG-0                           No  ...      tissue   
...                                         ...  ...         ...   
TTTGTCATCCACGCAG-283                         No  ...      tissue   
TTTGTCATCCGCTGTT-283                         No  ...      tissue   
TTTGTCATCGTCGTTC-283                         No  ...      tissue   
TTTGTCATCTGTACGA-283                         No  ...      tissue   
TTTGTCATCTTGCCGT-283                         No  ...      tissue   

                                                            cell_type  \
AACAGGGGTCGGATTT-0    CD14-positive, CD16-negative classical monocyte   
AACCAACGTCCGAAAG-0                                             B cell   
AACCTTTGTAGCACGA-0                                             B cell   
AAGCATCTCTATCGCC-0    CD14-positive, CD16-negative classical monocyte   
AATCACGGTCATAAAG-0                                             B cell   
...                                                               ...   
TTTGTCATCCACGCAG-283                                    megakaryocyte   
TTTGTCATCCGCTGTT-283       

In [12]:
from scdesigner.simulators import NegBinRegressionSimulator

model = NegBinRegressionSimulator(epochs=1, chunk_size=int(2e4), lr=0.01)

if run_full:
    model.fit(example_sce, "~ celltype")
else:
    example_sce = example_sce[:2000].to_memory()
    example_sce.X = example_sce.X.todense()
    model.fit(example_sce, "~ celltype")

In [13]:
print(model.params["coef_dispersion"].values.max())
model.params["coef_dispersion"][model.params["coef_dispersion"]>80]=80

0.040098116


In [14]:
from scdesigner.diagnose import compare_pca
import numpy as np

samples = model.sample(example_sce.obs.iloc[:2000, :])
compare_pca(example_sce[:2000].to_memory(), samples, np.log1p)

alt.FacetChart(...)